# Example of calibration using Jupyter-LAB

This tutorial requires the development branch of pyFAI, v0.22-dev or newer

In [ ]:
%matplotlib widget
import hdf5plugin
import h5py
import numpy
import pyFAI.calibrant
from pyFAI.gui.jupyter.calib import Calibration
from pyFAI.gui import jupyter
from pyFAI.units import hc
print(f"pyFAI version: {pyFAI.version}")

In [ ]:
# Read the dataset and the mask from  HDF5 file
with h5py.File("Calibration_Al2O3.h5") as h:
    data = h["data"][()]
    mask = h["mask"][()]
data.shape

In [ ]:
#max filter among all frames of the stack
img = numpy.max(data, axis=0)
img.shape

In [ ]:
# Display the image
_ = jupyter.display(img)

In [ ]:
# define some constants, especially the wavelength and the detector
energy = 13 #keV this is approximative and deserves fitting
wavelength = hc/energy*1e-10
eiger = pyFAI.detector_factory("Eiger4M")
print(f"Wavelength of the beam: {wavelength} A")

In [ ]:
# the calibrant and calibration object
corrundum = pyFAI.calibrant.CALIBRANT_FACTORY("alpha_Al2O3")
corrundum.wavelength = wavelength
eiger.mask = numpy.logical_or(mask, eiger.mask)
calib = Calibration(img, calibrant=corrundum, wavelength=wavelength, detector=eiger, mask=eiger.mask)

In [ ]:
# Here are the control points picked:
calib.peakPicker.points

In [ ]:
# Refinement of the geometry
calib.refine()
print("Cost function per control-point: ", calib.geoRef.chi2())

In [ ]:
#Enforce the SAXS mode and re-run the refinement with constrains
calib.geoRef.rot1 = calib.geoRef.rot2 = calib.geoRef.rot3 = 0
calib.fixed = ["wavelength", "rot1", "rot2", "rot3"]
calib.refine()
calib.geoRef.chi2()

In [ ]:
# re-extract control point along all possible rings
calib.extract_cpt()

In [ ]:
# refine (still with SAXS constrains
calib.refine()
print("Cost function per control-point: ", calib.geoRef.chi2())

In [ ]:
# remove some rings which are too weak or noisy
for group in "dfijk":
    calib.remove_grp(lbl=group)

In [ ]:
#refine with less rings (but better quality)
calib.refine()
print("Cost function per control-point: ", calib.geoRef.chi2())

In [ ]:
# Relax some constrains, i.e. fit even the energy
calib.fixed = ["rot3"]
calib.refine()
print("Cost function per control-point: ", calib.geoRef.chi2())
print(f"Refined energy of the incident beam: {calib.geoRef.energy} keV")

In [ ]:
# Generate a simple azimuthal integrator from the geometry refinement
ai = pyFAI.load(calib.geoRef)
ai

In [ ]:
# Perform and display the 1d integration
ax = jupyter.plot1d(ai.integrate1d(img, 1000), calibrant=corrundum)
ax.set_yscale("log")

In [ ]:
# Perform and display the 2d integration
ax = jupyter.plot2d(ai.integrate2d(img, 1000), calibrant=corrundum)

In [ ]:
#Some performance measurements for different integration methods
%timeit ai.integrate1d(img, 1000)

In [ ]:
%timeit ai.integrate1d(img, 1000, method=("bbox", "csr", "opencl"), error_model="poisson")

In [ ]:
%timeit ai.integrate2d(img, 1000)

In [ ]:
%timeit ai.integrate2d(img, 1000, method=("bbox", "csr", "opencl"), error_model="poisson")

In [ ]:
ai.guess_max_bins()

In [ ]:
ai.guess_max_bins(search_range=(2000,4000), 
                  radial_range=(4, 40))

This notebook demonstrated how to
* display powder diffraction images
* perform the geometry calibration
* integrate some frames and display the result